In [1]:
### Imports and configuration

# setup variables

import os
import json
import tqdm
from s2orc.config import CURRENT_VERSION

# jsonlines https://jsonlines.readthedocs.io/en/latest/#api
import jsonlines
import gzip
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import hiplot

LOCAL_S2ORC_DIR = 's2orc-data'

psychology_paper_dir = os.path.join(LOCAL_S2ORC_DIR, CURRENT_VERSION, 'psychology')
psychology_paper_suffix = 'psych.text.jsonl'

links_dir = os.path.join(LOCAL_S2ORC_DIR, CURRENT_VERSION, 'psych_links')
links_suffix = 'psych.text.link.jsonl'


In [2]:
## Get corpus into memory

start = 0
span = 100 # all: 1700

links = []

links_files = sorted(os.listdir(links_dir), key=lambda f: int(f.split('.')[0]))[start:(start+span)]
for link_file in tqdm.tqdm(links_files):
    with gzip.open(os.path.join(links_dir, link_file), 'rb') as f_in:
        batch_links = list(jsonlines.Reader(f_in))
        for link in batch_links:
            if link['citing_paper']['grobid_parse'].get('body_text') is not None and link['cited_paper']['grobid_parse'].get('body_text') is not None:
                links.append(link)

np.random.seed(2134234)
links = np.array(links)
np.random.shuffle(links)

100%|██████████| 100/100 [00:01<00:00, 58.22it/s]


# work on the data

In [3]:
from flair.embeddings import WordEmbeddings, DocumentPoolEmbeddings, TransformerDocumentEmbeddings
from flair.data import Sentence

In [153]:
import regex
from syntok.segmenter import split
from syntok.tokenizer import Tokenizer

token_filter_re = r'^\p{L}(\p{L}|\.|[0-9])+$'
science_blacklist = {'et', 'al', 'al.'} # remove words specific for scientific papers without any importance for the task

def filter_tokens(tokens):
    # Filter out non-common-word/non-real-world-entity tokens
    return [
        token for token in tokens if 
            regex.match(token_filter_re, token.text) 
            and token.text not in science_blacklist
    ]

author_re = r'(((de|De|van|Van|von|Von)\s+(\p{Ll}+\s+)?)?\p{Lu}(\p{Ll}|-)+)'

citation_re = (
               r'([(;,]|\s)'
            + author_re +
               r'(\s?((([&,]|and|\s)+\s?' + author_re + r')|(et al\.?)))?' # alternative second author
               r'('
                 r'([;,]|\s)+'
                 r'\s*[0-9]{4}\p{Ll}?\s*' # year
               r')+'
               r'([);,]|\s)'
              )

in_text_citation_re = (
    author_re + r'\s*\((\s*[0-9]{4}\p{Ll}?\s*,?)\)'
)
def filter_citations(text):
    n_subs_made = 1
    while n_subs_made > 0:
        text, n_subs_made = regex.subn(citation_re, ';', text)
        text, n_subs_made2 = regex.subn(citation_re, ';', text)
        n_subs_made += n_subs_made2
    return text

def process_section_to_chunks(text):
    chunksize = 1
    tokenized_sents = list(split(Tokenizer().tokenize(text)))
    sents = [' '.join(str(token) for token in sent) for sent in tokenized_sents]
    sents = [' '.join(sents[i:i+chunksize]) for i in range(len(sents)-chunksize)]
    sentences = []
    for sent in sents:
        sent = text_to_sentence(sent)
        if sent is not None:
            sentences.append(sent)
    return sentences

def text_to_sentence(text):
    text = filter_citations(text) 
    s = Sentence(text, use_tokenizer=True)
    s.tokens = filter_tokens(s.tokens)
    if len(s.tokens) > 0:
        return s
    else:
        return None

In [5]:
# extract the important information from the original S2ORC corpus format
def process_link(link, process_section):
    context = link['citation_context']
    citing_paper = link['citing_paper']
    cited_paper = link['cited_paper']
    
    parts = []
    for text_chunk in cited_paper['grobid_parse']['body_text']:
        text = text_chunk.get('text')
        if text is not None:
            chunk_parts = process_section(text)
            parts.extend(chunk_parts)
    citing_string = ''.join([context['pre_context'], context['context_string'], context['post_context']])
    return {
        'citing_str': context['context_string'],
        'citing_context': citing_string,
        'citing_context_part': text_to_sentence(citing_string),
        'cited_text_parts': parts,
    }


In [6]:
def calc_embedding_scores(link, metrics, embedding_name, embedding):
    all_sim = {}
    
    s = link['citing_context_part']
    embedding.embed(s)
    citation_embedding = s.embedding.detach().numpy()

    sentences = link['cited_text_parts']
    for sentence in sentences:
        embedding.embed(sentence)
        all_sim[sentence.to_plain_string()] = {}
        for name, metric in metrics.items():
            sim = 1 - metric(sentence.embedding.detach().numpy(), citation_embedding)
            full_name = '_'.join([embedding_name, name])
            all_sim[sentence.to_plain_string()][full_name] = sim
        sentence.clear_embeddings()
    s.clear_embeddings()
    
    return pd.DataFrame(all_sim).T


### Bag of words (unweighted)

In [7]:
def calc_bow_occurrence_score(link, name):
    scores = []
    s = Sentence(link['citing_context'], use_tokenizer=True)
    context_token_set = set(token.text for token in s.tokens)
    sentences = link['cited_text_parts']
    for sentence in sentences:
        sent_token_set = set(token.text for token in sentence.tokens)
        score = len(sent_token_set.intersection(context_token_set)) / len(sent_token_set.union(context_token_set))            
        scores.append(score)
    return pd.DataFrame({
        name: scores
    }, index=[sent.to_plain_string() for sent in sentences])

### Bag of words weighted by Inverse Term Frequency (with lemmatization)

In [156]:
from wordfreq import word_frequency
from collections import defaultdict
from nltk.stem import WordNetLemmatizer 
import skfuzzy as fuzz

def get_length_penalty(sent_len):
    # 0.5 value for len=2
    # quickly raising to 1 at ~10 words
    return fuzz.sigmf(sent_len, 2, 0.5)

def get_word_itf(string_tokens):
    min_val = 10e-7
    return [1./max(min_val, word_frequency(token, 'en')) for token in string_tokens]

def transform_tokens(string_tokens, lemmatizer):
    return [lemmatizer.lemmatize(token.lower()) for token in string_tokens]

def calc_bow_itf_score(link, name):
    """
    Score using term frequency
    """
    lemmatizer = WordNetLemmatizer()
    scores = []
    s = link['citing_context_part']
    s_tokens = [token.text for token in s.tokens]
    context_token_set = set(transform_tokens(s_tokens, lemmatizer=lemmatizer))
    sentences = link['cited_text_parts']
    for sentence in sentences:
        sent_tokens = [token.text for token in sentence.tokens]
        sent_token_set = set(transform_tokens(sent_tokens, lemmatizer))
        if len(sent_token_set) == 0:
            scores.append(0)
            continue
        matching_tokens = sent_token_set.intersection(context_token_set)
        all_tokens = sent_token_set.union(context_token_set)
        raw_score = np.sum(get_word_itf(matching_tokens)) / np.sum(get_word_itf(all_tokens))
        # Eliminate artifacts by penalizing extremely short matches
        raw_score *= get_length_penalty(len(sent_token_set))
        if np.isclose(raw_score, 0):
            score = 0.
        else:
            score = 1./-np.log(raw_score)
        scores.append(score)
    return pd.DataFrame({
        name: scores
    }, index=[sent.to_plain_string() for sent in sentences])


###  TS SS distance metric

In [9]:
from scipy.spatial import distance
from scipy.linalg import norm
from Vector_Similarity import *

def TS_SS(vec1, vec2) :
    val = Triangle(vec1, vec2) * Sector(vec1, vec2)
    return min(1, val/3)

def Triangle(vec1, vec2) :
    theta = math.radians(Theta(vec1,vec2))
    return (norm(vec1) * norm(vec2) * math.sin(theta)) / 2

def Theta(vec1, vec2) :
    return math.acos(1 - distance.cosine(vec1, vec2)) + math.radians(10)

def Magnitude_Difference(vec1, vec2) :
    return abs(norm(vec1) - norm(vec2))

def Sector(vec1, vec2) :
    ED = distance.euclidean(vec1, vec2)
    MD = Magnitude_Difference(vec1, vec2)
    theta = Theta(vec1, vec2)
    return math.pi * math.pow((ED+MD),2) * theta/360

2.23606797749979
0.9999999999999998
0.0004639582566999478


### Prepare data

In [10]:
bert_embedding = TransformerDocumentEmbeddings('bert-base-uncased', fine_tune=False)
roberta_embedding = TransformerDocumentEmbeddings('roberta-base', fine_tune=False)
glove_embedding = DocumentPoolEmbeddings([WordEmbeddings('glove')])

In [11]:
n_train_links = int(0.5 * len(links))
n_validation_links = int(0.2 * len(links))
n_test_links = len(links) - n_train_links - n_validation_links
train_links = links[:15]
validation_links = links[15:45]
test_links = links[-n_test_links:]
#links = None

In [12]:
import copy
def prepare_link_and_val(link, val_links):
    result = {"original" : process_link(link, process_section_to_chunks)}
    for i in range(len(val_links)):
        val_link = copy.deepcopy(val_links[i])
        val_link2 = copy.deepcopy(link)
        val_link2['citation_context'] = val_link['citation_context']
        val_link['citation_context'] = link['citation_context']
        result.update({
            "val_orig_context_"+str(i) : process_link(val_link, process_section_to_chunks),
            "val_orig_paper_"+str(i) : process_link(val_link2, process_section_to_chunks)
        })
    return result

### Score pipeline

In [147]:
from plot_text_sim import plot_text_sim 
from scipy.spatial import distance
import itertools
metrics = {"cos" : distance.cosine, "ts_ss" : TS_SS}

# do it in a function to prevent memory leaks
def calculate_similarities(train_links, validation_links):
    results = []
    for link, val_links in tqdm.tqdm(list(itertools.zip_longest(train_links, validation_links))):
        
        preprocessed = prepare_link_and_val(link, val_links or [])
        bow_itf = {name: calc_bow_itf_score(link, name='bow_itf_'+name) for name, link in preprocessed.items()}
        
        bert = {name: calc_embedding_scores(link, metrics, embedding_name='bert_'+name, embedding = bert_embedding) for name, link in preprocessed.items()}
        
        glove = {name: calc_embedding_scores(link, metrics, embedding_name='glove_'+name, embedding = glove_embedding) for name, link in preprocessed.items()}
        roberta = {name: calc_embedding_scores(link, metrics, embedding_name='roberta_'+name, embedding = roberta_embedding) for name, link in preprocessed.items()}
        bow_occur = {name: calc_bow_occurrence_score(link, name='bow_occurrence_'+name) for name, link in preprocessed.items()}
        
        data_emb = {name : pd.merge(pd.merge(glove[name], bert[name], left_index = True, right_index = True), roberta[name], left_index = True, right_index = True) for name, link in preprocessed.items()}
        data_bow = {name : pd.merge(bow_occur[name], bow_itf[name], left_index = True, right_index = True) for name, link in preprocessed.items()}
        data = {name : pd.merge(data_emb[name], data_bow[name], left_index = True, right_index = True) for name, link in preprocessed.items()}
#         data = {name : bow_itf[name] for name, link in preprocessed.items()}
        results.append({
            'citing_str': preprocessed['original']['citing_str'],
            'citing_context': preprocessed['original']['citing_context'],
            'data': data,
        })

    return results, preprocessed


In [ ]:

start = 12
span = 1
val_span = 2
val = np.split(validation_links[start:start+val_span*span], span)
train = train_links[start:start+span]
results, preprocessed = calculate_similarities(train, val)

In [14]:
processed_results = copy.deepcopy(results)

for result in processed_results:
    df = result['data']['original']
    df['bert_original_cos_ampl'] = df['bert_original_cos']**6
    df['comb_bow_itf_bert_cos'] = np.sqrt(df['bow_itf_original'] * df['bert_original_cos_ampl'])
    df['comb_bow_itf_bert_ts_ss'] = np.sqrt(df['bow_itf_original'] * df['bert_original_ts_ss'])
    # derive weighted moving average
    for column in df.columns:
        df[f'{column}_rolling'] = df[column].rolling(4, center=True, win_type='gaussian').mean(std=2)


NameError: name 'results' is not defined

In [ ]:
processed_results = copy.deepcopy(results)

for result in processed_results:
    df = result['data']['original']
    df['comb_bow_itf_bert'] = np.sqrt(df['bow_itf_original'] * (1 - df['bert_original_cos'])**4)
    df['comb_bow_itf_glove'] = np.sqrt(df['bow_itf_original'] * (1 - df['glove_original_cos'])**4)
    df['comb_bow_itf_roberta'] = np.sqrt(df['bow_itf_original'] * (1 - df['roberta_original_cos'])**4)
    # derive weighted moving average
    for column in df.columns:
        df[f'{column}_rolling'] = df[column].rolling(4, center=True, win_type='gaussian').mean(std=2)

In [ ]:
import pickle
with open("results_emb_bow.p", "wb") as file:
    pickle.dump(processed_results, file)

In [ ]:
with open("preprocessed_.p", "wb") as file:
    pickle.dump(preprocessed, file)

In [ ]:
def mean_results(results):
    return{
        name : {
            column : np.mean(df[column]) for column in df.columns if df[column].dtype == float
        } for name, df in results.items()
    }

In [ ]:
mean_res = mean_results(results[0]["data"])

In [ ]:
with open("results_mean.p", "wb") as file:
    pickle.dump(mean_res, file)

In [ ]:
process_link(train_links[start], process_section_to_chunks)['citing_str'] 

In [15]:
import hiplot as hip
result_df = results[0]['data']['original'].assign(text_beginning = lambda df: df.index.str[:10])
exp = hip.Experiment.from_dataframe(result_df)
displayed_exp = exp.display()

NameError: name 'results' is not defined

In [157]:
_test_results, _test_preprocessed = calculate_similarities([test[2]], [])


  0%|          | 0/1 [00:00<?, ?it/s]

{'opposed', 'item', 'diesendruck', 'our', 'that', 'hammer', 'are', 'from', 'can', 'be', 'category', 'a', 'the', 'is', 'one', 'improved', 'to', 'available', 'researcher', 'time', 'learning', 'two', 'studying', 'motivated', 'gentner', 'data', 'weinshall', 'this', 'presented', 'article', 'of', 'hypothesis', 'publicly', 'have', 'osf.io', 'in', 'at', 'vh7pn', 'demonstrated', 'study', 'by', 'same', 'simultaneously', 'http'}
637
{'the', 'that', 'are', 'from', 'by', 'to', 'of'}
{'in', 'one', 'is', 'to', 'this', 'of'}
{'be', 'the', 'that', 'is', 'one', 'in', 'from', 'by', 'to', 'of'}
{'the'}
{'the', 'two', 'at', 'by', 'same', 'of'}
{'to', 'be', 'of', 'the'}
{'be', 'the', 'learning', 'in', 'from', 'by', 'of'}
{'by', 'is', 'of', 'the'}
{'to', 'study', 'that', 'the'}
{'to', 'are', 'the'}
{'of', 'in', 'from', 'the'}
{'to', 'of', 'our', 'the'}
{'a'}
{'a', 'the', 'that', 'is', 'by', 'to', 'of'}
{'the', 'in', 'is', 'that', 'to'}
{'the', 'have', 'study', 'to', 'of'}
{'the', 'gentner', 'have', 'that', '

{'be', 'the', 'two', 'that', 'in', 'to', 'this', 'of'}
{'the', 'in', 'at', 'that', 'are'}
{'to', 'have', 'our', 'the'}
{'the', 'in', 'one', 'to', 'of'}
{'be', 'the', 'are', 'to', 'of'}
{'a', 'the', 'are', 'to', 'of'}
{'a', 'the', 'one', 'this', 'of'}
{'be', 'the', 'that', 'at', 'are', 'from', 'to', 'can'}
{'that', 'at', 'one', 'to', 'of'}
{'a', 'the', 'our', 'is', 'in', 'to', 'can', 'of'}
{'of', 'be', 'that', 'at'}
{'this', 'hypothesis', 'study', 'the'}
{'be', 'a', 'the', 'to', 'of'}
{'the', 'in', 'at', 'to', 'this', 'of'}
{'be', 'our', 'that', 'from', 'to', 'this'}
{'is', 'the'}
{'be', 'a', 'the', 'our', 'that', 'is', 'in', 'from', 'by', 'same', 'to'}
{'in', 'a', 'the'}
{'the', 'in', 'is', 'to', 'of'}
{'be', 'in', 'that', 'the'}
{'of', 'in', 'the'}
{'the', 'learning', 'that', 'is', 'in', 'are', 'to', 'of'}
{'be', 'a', 'the', 'from', 'to', 'of'}
{'be', 'the', 'in', 'is', 'by', 'to', 'of'}
{'have'}
{'to', 'be', 'of'}
{'to', 'of', 'is'}
{'to', 'a', 'the'}
{'be', 'the', 'our', 'is', 'by',

  0%|          | 0/1 [00:11<?, ?it/s]


KeyboardInterrupt: 

### Slightly wider manual comparison

In [160]:
start = 0
span = 10
test = test_links[start:start+span]

test_results, test_preprocessed = calculate_similarities(test, [])

processed_test_results = copy.deepcopy(test_results)

for result in processed_test_results:
    df = result['data']['original']
    df['bert_original_cos_ampl'] = df['bert_original_cos']**6
    df['comb_bow_itf_bert_cos'] = np.sqrt(df['bow_itf_original'] * df['bert_original_cos_ampl'])
    df['comb_bow_itf_bert_ts_ss'] = np.sqrt(df['bow_itf_original'] * df['bert_original_ts_ss'])
    # derive weighted moving average
    for column in df.columns:
        df[f'{column}_rolling'] = df[column].rolling(4, center=True, win_type='gaussian').mean(std=2)


  0%|          | 0/10 [00:00<?, ?it/s]

{'equivalent', 'usually', 'on', 'rohrer', 'found', 'massed', 'last', 'and', 'that', 'spacing', 'repeated', 'without', 'vul', 'due', 'the', 'failed', 'pashler', 'improves', 'is', 'effort', 'report', 'only', 'to', 'well', 'refers', 'researcher', 'rely', 'been', 'documented', 'practice', 'learning', 'not', 'review', 'experiment', 'comparison', 'century', 'wixted', 'spaced', 'retention', 'significant', 'achieve', 'presentation', 'statistically', 'of', 'literature.over', 'information', 'see', 'mental', 'have', 'in', 'evaluated', 'meaningful', 'cepeda', 'by', 'effect', 'which'}
444
{'researcher', 'practice', 'the', 'in', 'to'}
set()
{'practice', 'the', 'learning', 'and', 'of'}
{'found', 'practice', 'learning', 'and', 'that', 'is', 'review'}
{'the', 'practice', 'is', 'effect', 'of'}
{'the', 'practice', 'failed', 'and', 'that', 'review', 'in', 'spacing', 'retention', 'to', 'of'}
{'information', 'practice', 'the', 'and', 'review', 'not', 'retention', 'effect', 'to', 'which', 'of'}
{'to', 'ceped

 10%|█         | 1/10 [01:28<13:18, 88.70s/it]

{'on', 'thus', 'effect', 'and', 'training', 'primate', 'present', 'rodent', 'also', 'a', 'the', 'between', 'analog', 'moreover', 'is', 'some', 'used', 'for', 'discrimination', 'we', 'ha', 'cocaine', 'been', 'mechanism', 'comparison', 'stimulus', 'allowing', 'primarily', 'examining', 'dopaminergic', 'of', 'addition', 'methamphetamine', 'mediated', 'amphetamine', 'drug', 'in', 'study', 'cathinone', 'determined', 'by', 'direct', 'examined', 'translational'}
128
{'been', 'a', 'the', 'and', 'in'}
{'on', 'the', 'in', 'is', 'cathinone', 'used', 'of'}
{'effect', 'and', 'been'}
{'and', 'of'}
{'cocaine', 'amphetamine', 'and', 'stimulus', 'effect', 'for', 'of'}
{'amphetamine', 'cocaine', 'and', 'in', 'methamphetamine'}
{'and', 'in'}
{'been', 'a', 'drug', 'and', 'of'}
{'ha', 'been', 'and', 'in', 'of'}
{'been', 'the', 'and', 'in', 'of'}
{'of', 'is'}
{'of', 'ha', 'and', 'been'}
{'on', 'mechanism', 'drug', 'and', 'is', 'effect', 'of'}
{'of', 'a', 'the', 'and', 'present', 'methamphetamine'}
{'on', 'th

 20%|██        | 2/10 [01:53<09:16, 69.60s/it]

...

{'regarding', 'current', 'research', 'leading', 'and', 'dechurch', 'le', 'our', 'leaf', 'important', 'performance', 'author', 'a', 'the', 'wa', 'practitioner', 'with', 'is', 'pearsall', 'tmms', 'order', 'to', 'therefore', 'much', 'about', 'many', 'for', 'human', 'tmm', 'mark', 'team', 'absence', 'foster', 'this', 'of', 'organization', 'information', 'how', 'little', 'suggest', 'area', 'improve', 'their', 'purpose', 'resource', 'yet', 'e.g.', 'in', 'future', 'known', 'antecedent', 'literature', 'mesmermagnus', 'an'}
166
{'area', 'and', 'team', 'for', 'of', 'organization'}
{'the', 'and', 'team', 'to', 'of', 'organization'}
{'their', 'and', 'team', 'in', 'order', 'to', 'of'}
{'information', 'the', 'their', 'and', 'team', 'to', 'of'}
{'literature', 'and', 'team', 'the'}
{'the', 'their', 'and', 'team', 'to', 'about', 'of'}
{'information', 'the', 'and', 'with', 'team', 'is', 'in', 'to', 'for', 'of'}
{'performance', 'research', 'a', 'the', 'their', 'and', 'mark', 'team', 'in', 'yet', 'anteced

 90%|█████████ | 9/10 [09:25<01:01, 61.41s/it]

{'asked', 'current', 'were', 'and', 'are', 'circumstance', 'from', 'answer', 'learner', 'respond', 'the', 'with', 'knowledge', 'main', 'holyoak', 'to', 'eye', 'two', 'analogous', 'problem', 'extension', 'meaning', 'presented', 'of', 'explain', 'how', 'reader', 'adapted', 'blind', 'test', 'analogical', 'convergence', 'gick', 'through', 'derived', 'story', 'participant', 'his', 'character'}
637
{'the', 'are', 'from', 'to', 'of'}
{'to', 'and', 'problem', 'of'}
{'the', 'and', 'analogical', 'knowledge', 'from', 'to', 'of'}
{'analogical', 'the'}
{'two', 'and', 'of', 'the'}
{'to', 'and', 'of', 'the'}
{'of', 'and', 'from', 'the'}
{'and', 'of', 'the'}
{'to', 'analogical', 'problem', 'the'}
{'how', 'the', 'and', 'are', 'problem', 'to'}
{'the', 'and', 'problem', 'from', 'of'}
{'the', 'and', 'analogical', 'problem', 'to', 'of'}
{'analogical'}
{'the', 'and', 'analogical', 'to', 'of'}
{'to', 'problem', 'the'}
{'to', 'of', 'problem', 'the'}
{'the', 'and', 'problem', 'to', 'of'}
{'the', 'are', 'proble

{'the', 'and', 'analogical', 'problem', 'to', 'of'}
{'to', 'of', 'the'}
{'the', 'two', 'problem', 'from', 'of'}
{'the', 'test', 'story', 'to', 'character', 'of'}
set()
{'to', 'of', 'the'}
{'to', 'and', 'the'}
{'and', 'the'}
{'to', 'the'}
{'the'}
{'to', 'and', 'were', 'the'}
{'the'}
{'and', 'with', 'of', 'the'}
set()
{'two', 'were', 'from', 'the'}
{'two', 'to', 'of'}
{'to', 'of', 'the'}
{'to', 'were', 'the'}
{'to', 'of'}
{'to'}
{'to', 'and', 'of', 'the'}
{'and', 'of', 'the'}
{'to', 'and', 'of', 'the'}
{'and', 'the'}
{'two', 'and', 'from', 'the'}
{'to', 'the'}
{'and'}
{'from', 'the'}
{'and', 'of', 'the'}
{'through', 'to', 'the'}
{'to', 'the'}
{'his', 'the'}
{'his', 'to', 'of', 'the'}
{'of', 'the'}
{'were', 'the', 'and', 'from', 'his', 'to', 'of'}
{'the'}
{'the'}
{'to', 'the'}
{'the'}
{'the', 'and', 'his', 'to', 'of'}
{'and', 'the'}
{'to', 'the'}
{'and', 'the'}
{'the'}
{'and', 'the'}
{'his', 'to', 'and', 'the'}
{'to'}
{'the'}
{'of', 'the'}
{'to', 'of', 'the'}
{'and'}
{'the'}
{'the'}
{'the

100%|██████████| 10/10 [11:28<00:00, 68.87s/it]


In [164]:
import pickle
with open("results_emb_bow_test.p", "wb") as file:
    pickle.dump(processed_test_results, file)

In [103]:
from scipy import stats
stats.spearmanr(df['bert_original_cos_ampl'],df['bert_original_ts_ss'] )

SpearmanrResult(correlation=0.9898346133962346, pvalue=0.0)

In [161]:

def display_best(df, column):
    print(f'\n-- {column.upper()} --')
    print(*[f'{i+1}: "{chunk}"' 
            for i, chunk in enumerate(df[column].sort_values(ascending=False).index.values.tolist()[:5])
           ],
          sep='\n'
         )
    
for result in processed_test_results:
    result['citing_str']
    result['citing_context']
    df = result['data']['original']
    display_best(df, 'bow_itf_original')
    display_best(df, 'bert_original_ts_ss')
    display_best(df, 'comb_bow_itf_bert_ts_ss')


'Cepeda, Pashler, Vul, Wixted, & Rohrer (2006)'

'rely on the effects of mental effort, comparisons have not been well documented in the literature.Over the last century learning researchers have found that spaced practice improves information retention (see review by Dempster, 1988) . In a report by Cepeda, Pashler, Vul, Wixted, & Rohrer (2006) of 271 spaced practice experiments, only 4.4% failed to achieve meaningful and statistically significant spacing effects. Information retention due to spaced practice is usually evaluated in comparison to massed practice, which refers to repeated presentation of equivalent information without'


-- BOW_ITF_ORIGINAL --
1: "The term spacing effect refers to enhanced learning during spaced as compared to massed study episodes for given item"
2: "Only of comparisons of massed and spaced performance showed no effect or negative effect from spacing making the spacing effect quite robust"
3: "The interaction between magnitude of the spacing effect and retention interval was examined by calculating the difference in performance between massed and spaced presentations and collapsing over each of seven retention interval ranges"
4: "The spacing effect hinges upon comparison of massed and spaced presentations of to be learned item"
5: "Because these and other theories are able to make differential predictions for spaced vs massed presentations as well as for changes in lag our theoretical discussion applies to both spacing and lag effects"

-- BERT_ORIGINAL_TS_SS --
1: "In spite of abundant evidence for distributed practice benefits number of empirical studies e.g and recent review of t

'(Gatch et al. 2015;'

'used in the present study is primarily mediated by dopaminergic mechanisms. Moreover, cocaine has also been used as the training stimulus in rodent drug discrimination studies examining some of the amphetamine and cathinone analogs examined in the present study (Gatch et al. 2015; Gatch et al. 2013; Glennon and Young 1984b) , thus allowing for a direct translational comparison between rodents and non-human primates. For comparison, we also determined the effects of a 3,4-methylenedioxy addition on the cocaine-like effects of methamphetamine (3,4-methylenedioxymethamphetamine;'

...

'Yet much less is known about TMM antecedents, leading many authors to suggest this as an important area for future research (e.g., DeChurch & MesmerMagnus, 2010; Lim & Klein, 2006; Marks, Zaccaro, & Mathieu, 2000; Mohammed et al., 2010; Pearsall, Ellis, & Bell, 2010) . This absence of information in the literature leaves organizations and human resource practitioners with little information regarding how to foster TMMs in order to improve the performance of their teams. Therefore, our purpose in the current research was'


-- BOW_ITF_ORIGINAL --
1: "Although significant research has focused on exploring the potential benefits of these two cognitions on outcomes such as team performance and satisfaction e.g Edwards Day as well as identifying their potential antecedents e.g Marks Marks Sabella the processes and developmental phases underlying their emergence in newly formed teams have yet to be explored e.g Ilgen"
2: "Next teams performed an additional minute experimental task during which team performance was assessed"
3: "While they were aware that the vehicles and knowledge about the tracks was divided among the team members they did not initially know which area of responsibility and expertise the other members possessed"
4: "Each team member was given sheet that illustrated his or her own specific role which they were able to keep during the experimental task"
5: "The individual members responses were averaged to create team score which was standardized for comparison"

-- BERT_ORIGINAL_TS_SS --
1: "

'Gick and Holyoak (1983)'

'The knowledge extension test presented learners with a convergence problem adapted from Gick and Holyoak (1983) . Through the eyes of the main character two analogical stories are presented to the reader. Participants were asked to explain how the character derived meaning from the analogous stories to respond to his current circumstance. Answers were blind'


-- BOW_ITF_ORIGINAL --
1: "Gick and Holyoak tested variety of such control groups which received either an irrelevant story that was not analogous to the radiation problem or no story at all no more than of such subjects ever produced the convergence solution"
2: "We should note however that Gick and Holyoak used both between subject and within subject procedures in different experiments and obtained essentially the same estimates of the percentage of subjects who could apply the analogy compare their Experiments II and"
3: "As noted above Gick and Holyoak presented an initial story analogy to subjects in the guise of recall experiment"
4: "The basic procedure used to separate spontaneous noticing of an analogy from its application after hint was adapted from Gick and Holyoak and was used in all of the present experiments"
5: "We will discuss the Gick and Holyoak study in more detail since it led directly to the present investigation"

-- BERT_ORIGINAL_TS_SS --
1: "Subjects were told 

In [162]:



for result in processed_test_results:
    result['citing_str']
    result['citing_context']
    df = result['data']['original']
    _ = plot_text_sim(df['bow_itf_original'], df.index, title='bow_itf')
    _ = plot_text_sim(df['bert_original_cos_ampl'], df.index, title='bert_cos')
    _ = plot_text_sim(df['bert_original_ts_ss'], df.index, title='bert_ts_ss')
    _ = plot_text_sim(df['comb_bow_itf_bert_cos'], df.index, title='comb_bow_itf_bert_cos')
    _ = plot_text_sim(df['comb_bow_itf_bert_ts_ss'], df.index, title='comb_bow_itf_bert_ts_ss')



'Cepeda, Pashler, Vul, Wixted, & Rohrer (2006)'

'rely on the effects of mental effort, comparisons have not been well documented in the literature.Over the last century learning researchers have found that spaced practice improves information retention (see review by Dempster, 1988) . In a report by Cepeda, Pashler, Vul, Wixted, & Rohrer (2006) of 271 spaced practice experiments, only 4.4% failed to achieve meaningful and statistically significant spacing effects. Information retention due to spaced practice is usually evaluated in comparison to massed practice, which refers to repeated presentation of equivalent information without'

'(Gatch et al. 2015;'

'used in the present study is primarily mediated by dopaminergic mechanisms. Moreover, cocaine has also been used as the training stimulus in rodent drug discrimination studies examining some of the amphetamine and cathinone analogs examined in the present study (Gatch et al. 2015; Gatch et al. 2013; Glennon and Young 1984b) , thus allowing for a direct translational comparison between rodents and non-human primates. For comparison, we also determined the effects of a 3,4-methylenedioxy addition on the cocaine-like effects of methamphetamine (3,4-methylenedioxymethamphetamine;'

'Gick & Holyoak, 1983;'

...

'locomotion. Attributing the specific patterns of fixation under the wheelchair condition to unfamiliarity with wheelchair use is indirectly supported by the findings demonstrating that a great deal of practice is necessary to effectively use optical variables in motor control (Michaels and de Vries, 1998; Jacobs et al., 2001; Fajen and Devaney, 2006) . This is referred to as perceptual attunement. The existence of perceptual attunement has been demonstrated with perceptual-motor tasks, such as judging optic angles or the expansion rate of an approaching'

'Pearsall, Ellis, & Bell, 2010)'

'Yet much less is known about TMM antecedents, leading many authors to suggest this as an important area for future research (e.g., DeChurch & MesmerMagnus, 2010; Lim & Klein, 2006; Marks, Zaccaro, & Mathieu, 2000; Mohammed et al., 2010; Pearsall, Ellis, & Bell, 2010) . This absence of information in the literature leaves organizations and human resource practitioners with little information regarding how to foster TMMs in order to improve the performance of their teams. Therefore, our purpose in the current research was'

'Gick and Holyoak (1983)'

'The knowledge extension test presented learners with a convergence problem adapted from Gick and Holyoak (1983) . Through the eyes of the main character two analogical stories are presented to the reader. Participants were asked to explain how the character derived meaning from the analogous stories to respond to his current circumstance. Answers were blind'